In [50]:
from IPython import display
import subprocess
import tempfile
import contextlib
import shutil
import pathlib
import time
import functools
from tqdm import notebook as tqdm_nb

In [51]:
@contextlib.contextmanager
def temp_dir():
    try:
        dirname = pathlib.Path(tempfile.mkdtemp())
        yield dirname
    finally:
        shutil.rmtree(dirname)

In [52]:
def say(words):
    with temp_dir() as dirname:
        fname = dirname / "words.wav"
        subprocess.run(["espeak-ng", "-v", "belinda", "-w", str(fname), words])
        display.display(display.Audio(str(fname), autoplay=True))

In [53]:
@functools.singledispatch
def run_step(value, pbar, dry_run):
    raise NotImplementedError(value)

@run_step.register(str)
def run_step_words(value, update, caller):
    caller(time.sleep, 0.2)
    update(2)
    caller(say, value)
    update(10)

@run_step.register(int)
@run_step.register(float)
def run_step_time(value, update, caller):
    for i in range(int(value * 10)):
        caller(time.sleep, 0.1)
        update(1)

In [54]:
def get_total(steps):
    caller = lambda func, value: None
    bits = []
    update = bits.append
    for value in steps:
        run_step(value, update, caller)
    return sum(bits)

In [58]:
def run_steps(name, steps):
    caller = lambda func, value: func(value)
    total = get_total(steps)
    pbar = tqdm_nb.tqdm(total=total, desc=name)
    update = pbar.update
    for value in steps:
        run_step(value, update, caller)
    say(name + " is done")

# Five Mindful Practices

## STOP

In [56]:
run_steps("STOP", [ 
    "Stand up and breathe.",
    5,
    "Feel your connection to the earth.",
    10,
    "Tune in to your body.",
    2,
    "Lower your gaze",
    5,
    "Scan your body and notice physical sensations or emotions.",
    10,
    "Discharge any unpleasant sensations, emotions or feelings on the out breath.",
    5,
    "Notice any pleasant ones and let them fill you up on the in breath.",
    10,
    "Observe.",
    0.5,
    "Lift your eyes and take in your surroundings.",
    5,
    "Observe something in your environment that is pleasant and be grateful for it and its beauty.",
    10,
    "Ask yourself what is possible or what is new or what is a forward step.",
    10,
])

## 9x9

In [57]:
run_steps("nine by nine", [
    "Name an object",
    2,
    "Breath in",
    4,
    "Breath out",
    4,
] * 9)

## Stroke your hands.

In [59]:
run_steps("Stroke your hands", [
    "Close your eyes.",
    2,
    "Take the index finger of your right hand and slowly move it up and down on the outside of your fingers.",
    30,
    "Swap hands",
    30,
])

## Loving-kindness meditation.

In [62]:
run_steps("Loving-kindness meditation", [
    "Say in your head",
    1,
    ] + [
    "May I be happy",
    4,
    "may I be well",
    4,
    "may I be filled with kindness",
    3,
    "and peace.",
    5
]*4)

## Mindful breathing for one minute.

In [65]:
run_steps("Mindful breathing", [
    "Close your eyes",
    3,
    "notice where you feel your breath.",
    3,
    "Focus on your breath.",
    3,
    "When your mind wanders, say 'thinking' and gently shepherd your attention back to your breath.",
    3,
    60,
])